In [468]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import json
import tensorflow as tf
from numpy import *
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from tensorflow.keras import layers,datasets
from sklearn.preprocessing import LabelEncoder,MinMaxScaler,StandardScaler
from tensorflow import keras
import gc
import warnings
warnings.filterwarnings('ignore')
import lightgbm as lgb
import category_encoders as ce
from sklearn.metrics import f1_score,classification_report,roc_auc_score

In [469]:
pd.set_option('display.max_columns', None)

In [470]:
plan_info = pd.read_csv('./ptom_third_plan.csv')
plan_info.dropna(how='all', inplace=True, axis=1)
plan_info.drop(['ad_start_time', 'ad_end_time', 'remark','origin'], axis=1, inplace=True)
plan_info.dropna(subset=['ad_info'],inplace=True)
plan_info.drop(['ad_id', 'ad_group_id', 'ad_name','media_id','plan_id','launch_op_id','bid_mode','bid_status','bid',
                'budget_mode','budget','opt_status','status','syn_time','update_time','inventory_type'], axis=1, inplace=True)
# 解析json
plan_info['ad_info'] = plan_info['ad_info'].apply(json.loads)
temp = plan_info['ad_info'].apply(pd.Series)
plan_info = pd.concat([plan_info,temp], axis=1)
plan_info.drop('ad_info', axis=1, inplace=True)
temp = plan_info['audience'].apply(pd.Series)
plan_info = pd.concat([plan_info,temp], axis=1)
plan_info.drop('audience', axis=1, inplace=True)
temp = plan_info['action'].apply(pd.Series)
plan_info = pd.concat([plan_info,temp], axis=1)
plan_info.drop('action', axis=1, inplace=True)
plan_info.dropna(how='all', inplace=True, axis=1)

plan_info_2 = plan_info.copy()
plan_info_2.drop(['game_package_batch_id','advanced_creative_type','game_package_desc','game_package_thumbnail_ids',
               'external_url','intelligent_flow_switch','audience_package_id','union_video_type','converted_time_duration',
               'roi_goal','device_type','deep_bid_type','auto_extend_targets'],axis=1,inplace=True)
plan_info_2.drop(['package','open_url','ad_modify_time','deep_cpabid','download_url','download_mode','id','campaign_id',
               'package','ad_create_time','start_time','ad_id','name','status','modify_time','advertiser_id','schedule_type','quick_app_url',
               'end_time','convert_id','audit_reject_reason','download_type','budget_mode','bid','pricing',
               'include_custom_actions','app_type','exclude_flow_package','aweme_fan_behaviors','business_ids','user_type',
               'activate_type','aweme_fan_accounts','aweme_fan_categories','aweme_fans_numbers','article_category',
                'flow_package','carrier','superior_popularity_type','device_brand','exclude_custom_actions','geolocation',
               'opt_status','learning_phase','district'],axis=1,inplace=True)
# 删除老版兴趣行为定向
plan_info_2.drop(['ad_tag','interest_tags','app_behavior_target','app_category','app_ids'],axis=1,inplace=True)
# 删除老版兴趣行为定向
plan_info_2.drop(['retargeting_tags'],axis=1,inplace=True)

In [559]:
image_info = pd.read_csv('./image_info.csv')
df = pd.merge(plan_info_2,image_info,on=['channel_id','source_id'],how='left')
df.dropna(subset=['image_id'],inplace=True)

In [560]:
df.rename(columns={'create_time_x':'create_time','create_time_y':'create_date'},inplace=True)
df = df[['ad_account_id', 'game_id', 'channel_id', 'source_id', 'create_time','create_date',
         'bid2','budget','inventory_type', 'schedule_time', 'delivery_range','flow_control_mode',
        'smart_bid_type', 'adjust_cpa', 'cpa_bid', 'hide_if_exists', 'hide_if_converted',
        'auto_extend_enabled', 'age','gender', 'city', 'location_type', 'platform', 'launch_price','retargeting_type',
         'retargeting_tags_include','retargeting_tags_exclude', 'ac', 'android_osv','ios_osv', 
        'interest_action_mode', 'interest_categories', 'interest_words',
       'action_categories', 'action_days', 'action_scene', 'action_words',
       'image_id', 'label_ids']]

In [561]:
launch_report = pd.read_csv('./launch_report.csv',usecols=['tdate','channel_id', 'source_id', 'amount',
       'create_role_num', 'pay_role_user_num', 'new_role_money'])
launch_report.sort_values(by='tdate',inplace=True)
launch_report.drop_duplicates(subset=['channel_id','source_id'],keep='first',inplace=True)
df = pd.merge(df, launch_report,on=['channel_id','source_id'],how='left')
df.drop(df[df['tdate'].isna()].index,inplace=True)
df['label'] = ((df['pay_role_user_num']>0)&(df['amount']>=500)).astype(int)
df['image_id'] = df['image_id'].astype('int')
df['create_time'] = pd.to_datetime(df['create_time'])

In [562]:
# 读取image不同窗口期的运营数据
image_train_data_1 = pd.read_csv('./image_data/train_data_1.csv')
image_train_data_1['im_create_role_pay_rate_1'] = image_train_data_1.apply(lambda x:0 if x.im_create_role_num_1==0 else 
                                                            x.im_pay_role_user_num_1 / x.im_create_role_num_1,axis=1)
image_train_data_1['im_create_role_cost_1'] = image_train_data_1.apply(lambda x:np.inf if x.im_create_role_num_1==0 else 
                                                            x.im_amount_1 / x.im_create_role_num_1,axis=1)
image_train_data_1['im_create_role_pay_cost_1'] = image_train_data_1.apply(lambda x:np.inf if x.im_pay_role_user_num_1==0 else 
                                                            x.im_amount_1 / x.im_pay_role_user_num_1,axis=1)
image_train_data_1['im_valid_source_rate_1'] = image_train_data_1.apply(lambda x:0 if x.im_source_num_1==0 else 
                                                            x.im_valid_source_num_1 / x.im_source_num_1,axis=1)
image_train_data_1.drop(['data_win_1','label_ids_1'],axis=1,inplace=True)
image_train_data_1.rename(columns={'model_run_datetime_1':'create_date','image_id_1':'image_id'},inplace=True)
df = pd.merge(df, image_train_data_1, on=['image_id','create_date'],how='left', validate='many_to_one')

image_train_data_3 = pd.read_csv('./image_data/train_data_3.csv')
image_train_data_3['im_create_role_pay_rate_3'] = image_train_data_3.apply(lambda x:0 if x.im_create_role_num_3==0 else 
                                                            x.im_pay_role_user_num_3 / x.im_create_role_num_3,axis=1)
image_train_data_3['im_create_role_cost_3'] = image_train_data_3.apply(lambda x:np.inf if x.im_create_role_num_3==0 else 
                                                            x.im_amount_3 / x.im_create_role_num_3,axis=1)
image_train_data_3['im_create_role_pay_cost_3'] = image_train_data_3.apply(lambda x:np.inf if x.im_pay_role_user_num_3==0 else 
                                                            x.im_amount_3 / x.im_pay_role_user_num_3,axis=1)
image_train_data_3['im_valid_source_rate_3'] = image_train_data_3.apply(lambda x:0 if x.im_source_num_3==0 else 
                                                            x.im_valid_source_num_3 / x.im_source_num_3,axis=1)
image_train_data_3.drop(['data_win_3','label_ids_3'],axis=1,inplace=True)
image_train_data_3.rename(columns={'model_run_datetime_3':'create_date','image_id_3':'image_id'},inplace=True)
df = pd.merge(df, image_train_data_3, on=['image_id','create_date'],how='left', validate='many_to_one')

image_train_data_7 = pd.read_csv('./image_data/train_data_7.csv')
image_train_data_7['im_create_role_pay_rate_7'] = image_train_data_7.apply(lambda x:0 if x.im_create_role_num_7==0 else 
                                                            x.im_pay_role_user_num_7 / x.im_create_role_num_7,axis=1)
image_train_data_7['im_create_role_cost_7'] = image_train_data_7.apply(lambda x:np.inf if x.im_create_role_num_7==0 else 
                                                            x.im_amount_7 / x.im_create_role_num_7,axis=1)

image_train_data_7['im_create_role_pay_cost_7'] = image_train_data_7.apply(lambda x:np.inf if x.im_pay_role_user_num_7==0 else 
                                                            x.im_amount_7 / x.im_pay_role_user_num_7,axis=1)
image_train_data_7['im_valid_source_rate_7'] = image_train_data_7.apply(lambda x:0 if x.im_source_num_7==0 else 
                                                            x.im_valid_source_num_7 / x.im_source_num_7,axis=1)
image_train_data_7.drop(['data_win_7','label_ids_7'],axis=1,inplace=True)
image_train_data_7.rename(columns={'model_run_datetime_7':'create_date','image_id_7':'image_id'},inplace=True)
df = pd.merge(df, image_train_data_7, on=['image_id','create_date'],how='left', validate='many_to_one')

In [563]:
# 读取ad_account不同窗口期的运营数据
ad_train_data_1 = pd.read_csv('./ad_data/train_data_1.csv')
ad_train_data_1['ad_create_role_pay_rate_1'] = ad_train_data_1.apply(lambda x:0 if x.ad_create_role_num_1==0 else 
                                                            x.ad_pay_role_user_num_1 / x.ad_create_role_num_1,axis=1)
ad_train_data_1['ad_create_role_cost_1'] = ad_train_data_1.apply(lambda x:np.inf if x.ad_create_role_num_1==0 else 
                                                            x.ad_amount_1 / x.ad_create_role_num_1,axis=1)

ad_train_data_1['ad_create_role_pay_cost_1'] = ad_train_data_1.apply(lambda x:np.inf if x.ad_pay_role_user_num_1==0 else 
                                                            x.ad_amount_1 / x.ad_pay_role_user_num_1,axis=1)
ad_train_data_1['ad_valid_source_rate_1'] = ad_train_data_1.apply(lambda x:0 if x.ad_source_num_1==0 else 
                                                            x.ad_valid_source_num_1 / x.ad_source_num_1,axis=1)
ad_train_data_1.drop(['data_win_1'],axis=1,inplace=True)
ad_train_data_1['model_run_datetime_1'] = pd.to_datetime(ad_train_data_1['model_run_datetime_1']).dt.date
ad_train_data_1.rename(columns={'model_run_datetime_1':'create_date','ad_account_id_1':'ad_account_id'},inplace=True)
df['create_date'] = pd.to_datetime(df['create_date']).dt.date
df = pd.merge(df, ad_train_data_1, on=['ad_account_id','create_date'],how='left', validate='many_to_one')

ad_train_data_3 = pd.read_csv('./ad_data/train_data_3.csv')
ad_train_data_3['ad_create_role_pay_rate_3'] = ad_train_data_3.apply(lambda x:0 if x.ad_create_role_num_3==0 else 
                                                            x.ad_pay_role_user_num_3 / x.ad_create_role_num_3,axis=1)
ad_train_data_3['ad_create_role_cost_3'] = ad_train_data_3.apply(lambda x:np.inf if x.ad_create_role_num_3==0 else 
                                                            x.ad_amount_3 / x.ad_create_role_num_3,axis=1)

ad_train_data_3['ad_create_role_pay_cost_3'] = ad_train_data_3.apply(lambda x:np.inf if x.ad_pay_role_user_num_3==0 else 
                                                            x.ad_amount_3 / x.ad_pay_role_user_num_3,axis=1)
ad_train_data_3['ad_valid_source_rate_3'] = ad_train_data_3.apply(lambda x:0 if x.ad_source_num_3==0 else 
                                                            x.ad_valid_source_num_3 / x.ad_source_num_3,axis=1)
ad_train_data_3.drop(['data_win_3'],axis=1,inplace=True)
ad_train_data_3['model_run_datetime_3'] = pd.to_datetime(ad_train_data_3['model_run_datetime_3']).dt.date
ad_train_data_3.rename(columns={'model_run_datetime_3':'create_date','ad_account_id_3':'ad_account_id'},inplace=True)
df = pd.merge(df, ad_train_data_3, on=['ad_account_id','create_date'],how='left', validate='many_to_one')

ad_train_data_7 = pd.read_csv('./ad_data/train_data_7.csv')
ad_train_data_7['ad_create_role_pay_rate_7'] = ad_train_data_7.apply(lambda x:0 if x.ad_create_role_num_7==0 else 
                                                            x.ad_pay_role_user_num_7 / x.ad_create_role_num_7,axis=1)
ad_train_data_7['ad_create_role_cost_7'] = ad_train_data_7.apply(lambda x:np.inf if x.ad_create_role_num_7==0 else 
                                                            x.ad_amount_7 / x.ad_create_role_num_7,axis=1)

ad_train_data_7['ad_create_role_pay_cost_7'] = ad_train_data_7.apply(lambda x:np.inf if x.ad_pay_role_user_num_7==0 else 
                                                            x.ad_amount_7 / x.ad_pay_role_user_num_7,axis=1)
ad_train_data_7['ad_valid_source_rate_7'] = ad_train_data_7.apply(lambda x:0 if x.ad_source_num_7==0 else 
                                                            x.ad_valid_source_num_7 / x.ad_source_num_7,axis=1)
ad_train_data_7.drop(['data_win_7'],axis=1,inplace=True)
ad_train_data_7['model_run_datetime_7'] = pd.to_datetime(ad_train_data_7['model_run_datetime_7']).dt.date
ad_train_data_7.rename(columns={'model_run_datetime_7':'create_date','ad_account_id_7':'ad_account_id'},inplace=True)
df = pd.merge(df, ad_train_data_7, on=['ad_account_id','create_date'],how='left', validate='many_to_one')

In [564]:
df.drop(['interest_words','action_words'],axis=1,inplace=True)
df.drop(['create_role_num','amount','pay_role_user_num','new_role_money'],axis=1,inplace=True)

In [565]:
df.drop(['channel_id','source_id','create_date','tdate'],axis=1,inplace=True)

In [566]:
df.head()

ad_account_id  game_id         create_time     bid2   budget  \
0           4003  1000840 2020-01-19 16:18:31  1135.73   5000.0   
1           4003  1000840 2020-01-19 16:18:31  1135.08   5000.0   
2           4003  1000840 2020-01-19 16:24:53  1128.21   5000.0   
3           4003  1000840 2020-01-20 14:35:23  1180.24   8000.0   
4           4003  1000840 2020-01-29 18:01:59  1377.89  10000.0   

                                      inventory_type  \
0                             [INVENTORY_UNION_SLOT]   
1        [UNION_BOUTIQUE_GAME, INVENTORY_UNION_SLOT]   
2        [UNION_BOUTIQUE_GAME, INVENTORY_UNION_SLOT]   
3                             [INVENTORY_UNION_SLOT]   
4  [INVENTORY_FEED, INVENTORY_HOTSOON_FEED, INVEN...   

                                       schedule_time delivery_range  \
0  1111111111111111111111111111111111111111111111...          UNION   
1  1111111111111111111111111111111111111111111111...        DEFAULT   
2  1111111111111111111111111111111111111111111111...        DEFAULT   
3  1111111111111111111111111111111111111111111111...          UNION   
4  1110000000000000000011111111111111111111111111...        DEFAULT   

        flow_control_mode          smart_bid_type  adjust_cpa  cpa_bid  \
0  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.73   
1  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.08   
2  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1128.21   
3  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1180.24   
4  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1377.89   

   hide_if_exists hide_if_converted  auto_extend_enabled  \
0               0                AD                    0   
1               0                AD                    0   
2               0                AD                    0   
3               0                AD                    0   
4               0                AD                    0   

                                                 age       gender  \
0  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
1  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
2  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
3  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
4  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   

                                                city location_type   platform  \
0                                                 []       CURRENT  [ANDROID]   
1                                                 []       CURRENT  [ANDROID]   
2                                                 []       CURRENT  [ANDROID]   
3                                                 []       CURRENT  [ANDROID]   
4  [11, 12, 13, 14, 15, 21, 22, 23, 31, 32, 33, 3...       CURRENT  [ANDROID]   

  launch_price retargeting_type retargeting_tags_include  \
0           []             NONE                       []   
1           []             NONE                       []   
2           []             NONE                       []   
3           []             NONE                       []   
4           []             NONE                       []   

  retargeting_tags_exclude  ac android_osv ios_osv interest_action_mode  \
0                       []  []        NONE    NONE            UNLIMITED   
1                       []  []        NONE    NONE            UNLIMITED   
2                       []  []        NONE    NONE            UNLIMITED   
3                       []  []        NONE    NONE            UNLIMITED   
4                       []  []        NONE    NONE            UNLIMITED   

  interest_categories action_categories  action_days action_scene  image_id  \
0                  []               NaN          NaN          NaN     19788   
1                  []               NaN          NaN          NaN     19783   
2                  []               NaN          NaN          NaN     19636   


In [286]:
# df['im_amount_3'] = pd.cut(df.im_amount_3, [float('-inf'), 5000,10000,30000,60000,100000,200000, 400000,float('inf')], labels=[1,2,3,4,5,6,7,8])
# df['im_pay_role_user_num_3'] = pd.cut(df.im_pay_role_user_num_3, [float('-inf'),5,10,20,100,300,600, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_create_role_num_3'] = pd.cut(df.im_create_role_num_3, [float('-inf'),100,250,500,1000,5000,15000, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_new_role_money_3'] = pd.cut(df.im_new_role_money_3, [float('-inf'), 200,1000,2000,4000,10000, 50000,100000,float('inf')], labels=[1,2,3,4,5,6,7,8])
# df['im_create_role_cost_3'] = pd.cut(df.im_create_role_cost_3, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
# df['im_create_role_pay_cost_3'] = pd.cut(df.im_create_role_pay_cost_3, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_source_num_3'] = pd.cut(df.im_source_num_3, [float('-inf'),4,10,20,30,60,float('inf')], labels=[1,2,3,4,5,6])
# df['im_valid_source_num_3'] = pd.cut(df.im_valid_source_num_3, [float('-inf'),1,3,5,8,12,float('inf')], labels=[1,2,3,4,5,6])

In [568]:
bucket_col = ['im_amount_1','im_pay_role_user_num_1','im_create_role_num_1','im_new_role_money_1','im_source_num_1','im_valid_source_num_1',
             'im_amount_3','im_pay_role_user_num_3','im_create_role_num_3','im_new_role_money_3','im_source_num_3','im_valid_source_num_3',
             'im_amount_7','im_pay_role_user_num_7','im_create_role_num_7','im_new_role_money_7','im_source_num_7','im_valid_source_num_7',
             'ad_amount_1','ad_pay_role_user_num_1','ad_create_role_num_1','ad_new_role_money_1','ad_source_num_1','ad_valid_source_num_1',
             'ad_amount_3','ad_pay_role_user_num_3','ad_create_role_num_3','ad_new_role_money_3','ad_source_num_3','ad_valid_source_num_3',
             'ad_amount_7','ad_pay_role_user_num_7','ad_create_role_num_7','ad_new_role_money_7','ad_source_num_7','ad_valid_source_num_7']

In [569]:
def optimal_binning_boundary(x: pd.Series, y: pd.Series, nan: float = -999.) -> list:
    '''
        利用决策树获得最优分箱的边界值列表
    '''
    boundary = []  # 待return的分箱边界值列表
    
    x = x.fillna(nan).values  # 填充缺失值
    y = y.values
    from sklearn.tree import DecisionTreeClassifier
    clf = DecisionTreeClassifier(criterion='entropy',    #“信息熵”最小化准则划分
                                 max_leaf_nodes=10,       # 最大叶子节点数
                                 min_samples_leaf=0.05)  # 叶子节点样本数量最小占比

    clf.fit(x.reshape(-1, 1), y)  # 训练决策树
    
    n_nodes = clf.tree_.node_count
    children_left = clf.tree_.children_left
    children_right = clf.tree_.children_right
    threshold = clf.tree_.threshold
    
    for i in range(n_nodes):
        if children_left[i] != children_right[i]:  # 获得决策树节点上的划分边界值
            boundary.append(threshold[i])

    boundary.sort()

    min_x = x.min()
    max_x = x.max() + 0.1  # +0.1是为了考虑后续groupby操作时，能包含特征最大值的样本
    boundary = [min_x] + boundary + [max_x]

    return boundary

In [570]:
def bucketed(df, bucket_col):
    for col in bucket_col:
        df[col] = df[col].astype(np.float32)
        bins = optimal_binning_boundary(x=df[col],
                             y=df['label'])
        df[col] = pd.cut(df[col], bins, labels=range(1,len(bins)))
        df[col] = df[col].astype(np.float32)
        df[col] = df[col].fillna(0)
    return df

In [571]:
df = bucketed(df, bucket_col)

In [572]:
df['im_create_role_cost_1'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['im_create_role_pay_cost_1'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
df['im_create_role_cost_3'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['im_create_role_pay_cost_3'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
df['im_create_role_cost_7'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['im_create_role_pay_cost_7'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
df['ad_create_role_cost_1'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['ad_create_role_pay_cost_1'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
df['ad_create_role_cost_3'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['ad_create_role_pay_cost_3'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
df['ad_create_role_cost_7'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
df['ad_create_role_pay_cost_7'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])

In [573]:
df.head()

ad_account_id  game_id         create_time     bid2   budget  \
0           4003  1000840 2020-01-19 16:18:31  1135.73   5000.0   
1           4003  1000840 2020-01-19 16:18:31  1135.08   5000.0   
2           4003  1000840 2020-01-19 16:24:53  1128.21   5000.0   
3           4003  1000840 2020-01-20 14:35:23  1180.24   8000.0   
4           4003  1000840 2020-01-29 18:01:59  1377.89  10000.0   

                                      inventory_type  \
0                             [INVENTORY_UNION_SLOT]   
1        [UNION_BOUTIQUE_GAME, INVENTORY_UNION_SLOT]   
2        [UNION_BOUTIQUE_GAME, INVENTORY_UNION_SLOT]   
3                             [INVENTORY_UNION_SLOT]   
4  [INVENTORY_FEED, INVENTORY_HOTSOON_FEED, INVEN...   

                                       schedule_time delivery_range  \
0  1111111111111111111111111111111111111111111111...          UNION   
1  1111111111111111111111111111111111111111111111...        DEFAULT   
2  1111111111111111111111111111111111111111111111...        DEFAULT   
3  1111111111111111111111111111111111111111111111...          UNION   
4  1110000000000000000011111111111111111111111111...        DEFAULT   

        flow_control_mode          smart_bid_type  adjust_cpa  cpa_bid  \
0  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.73   
1  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.08   
2  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1128.21   
3  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1180.24   
4  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1377.89   

   hide_if_exists hide_if_converted  auto_extend_enabled  \
0               0                AD                    0   
1               0                AD                    0   
2               0                AD                    0   
3               0                AD                    0   
4               0                AD                    0   

                                                 age       gender  \
0  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
1  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
2  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
3  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   
4  [AGE_BETWEEN_24_30, AGE_BETWEEN_31_40, AGE_BET...  GENDER_MALE   

                                                city location_type   platform  \
0                                                 []       CURRENT  [ANDROID]   
1                                                 []       CURRENT  [ANDROID]   
2                                                 []       CURRENT  [ANDROID]   
3                                                 []       CURRENT  [ANDROID]   
4  [11, 12, 13, 14, 15, 21, 22, 23, 31, 32, 33, 3...       CURRENT  [ANDROID]   

  launch_price retargeting_type retargeting_tags_include  \
0           []             NONE                       []   
1           []             NONE                       []   
2           []             NONE                       []   
3           []             NONE                       []   
4           []             NONE                       []   

  retargeting_tags_exclude  ac android_osv ios_osv interest_action_mode  \
0                       []  []        NONE    NONE            UNLIMITED   
1                       []  []        NONE    NONE            UNLIMITED   
2                       []  []        NONE    NONE            UNLIMITED   
3                       []  []        NONE    NONE            UNLIMITED   
4                       []  []        NONE    NONE            UNLIMITED   

  interest_categories action_categories  action_days action_scene  image_id  \
0                  []               NaN          NaN          NaN     19788   
1                  []               NaN          NaN          NaN     19783   
2                  []               NaN          NaN          NaN     19636   


In [ ]:
# df['im_amount_1'] = pd.cut(df.im_amount_1, [float('-inf'), 3000,5800,17500,35000,60000,120000, 240000,float('inf')], labels=[1,2,3,4,5,6,7,8])
# df['im_pay_role_user_num_1'] = pd.cut(df.im_pay_role_user_num_1, [float('-inf'),2,4,6,30,90,180, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_create_role_num_1'] = pd.cut(df.im_create_role_num_1, [float('-inf'),100,250,500,1000,5000,15000, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_new_role_money_1'] = pd.cut(df.im_new_role_money_1, [float('-inf'), 200,1000,2000,4000,10000, 50000,100000,float('inf')], labels=[1,2,3,4,5,6,7,8])
# df['im_create_role_cost_1'] = pd.cut(df.im_create_role_cost_1, [float('-inf'), 20,40,60,80,100, float('inf')], labels=[1,2,3,4,5,6])
# df['im_create_role_pay_cost_1'] = pd.cut(df.im_create_role_pay_cost_1, [float('-inf'),3000,4000,5000,6000,8000,10000, float('inf')], labels=[1,2,3,4,5,6,7])
# df['im_source_num_1'] = pd.cut(df.im_source_num_1, [float('-inf'),4,10,20,30,60,float('inf')], labels=[1,2,3,4,5,6])
# df['im_valid_source_num_1'] = pd.cut(df.im_valid_source_num_1, [float('-inf'),1,3,5,8,12,float('inf')], labels=[1,2,3,4,5,6])

In [574]:
def get_mutil_feature(data):
    '''
    多值离散特征mutil_hot
    '''
    cols_mutil = ['inventory_type','age','city','retargeting_tags_include','retargeting_tags_exclude','ac','interest_categories',
       'action_scene','action_categories']
    for col in cols_mutil:
        if col in ['inventory_type','age']:
            data[col] = data[col].apply(lambda x:x if x==x else [])
            data = data.join(data[col].str.join('|').str.get_dummies().add_prefix(col+'_'))
            
            data.drop(col,axis=1,inplace=True)
        else:
            data[col] = data[col].apply(lambda x:x if x==x else [])
            data[col]=data[col].apply(lambda x:[str(i) for i in x])
            data = data.join(data[col].str.join('|').str.get_dummies().add_prefix(col+'_'))
            data.drop(col,axis=1,inplace=True)
    return data

In [481]:
# 对列表内容进行编码降维
# def get_mutil_feature(data):
#     cols = ['inventory_type','age','city','retargeting_tags_include','retargeting_tags_exclude','ac','interest_categories',
#        'action_scene','action_categories']
#     for col in cols:
#         if col in ['inventory_type','age']:
#             data[col] = data[col].apply(lambda x:x if x==x else [])
#             data = data.join(data[col].str.join('|').str.get_dummies().add_prefix(col+'_'))
#             data.drop(col,axis=1,inplace=True)
#         elif col in ['city','retargeting_tags_include','retargeting_tags_exclude','interest_categories','action_categories']:
#             data[col] = data[col].apply(lambda x:x if x==x else [])
#             data[col]=data[col].apply(lambda x:[str(i) for i in x])
#             temp = data[col].str.join('|').str.get_dummies()
#     #         print(temp.shape[1])
#             pca = PCA(n_components=0.9)
#             temp = pca.fit_transform(temp.values)
#             temp = pd.DataFrame(temp,columns = [col+str(i) for i in range(temp.shape[1])])
#     #         print(temp.shape[1])
#             data = data.join(temp)
#             del temp
#             data.drop(col,axis=1,inplace=True)
#         else:
#             data[col] = data[col].apply(lambda x:x if x==x else [])
#             data[col]=data[col].apply(lambda x:[str(i) for i in x])
#             data = data.join(data[col].str.join('|').str.get_dummies().add_prefix(col+'_'))
#             data.drop(col,axis=1,inplace=True)
    
#     gc.collect()
#     return data

In [575]:
%%time
df = get_mutil_feature(df)

Wall time: 52.9 s


In [576]:
df.shape

(28562, 2478)

In [577]:
df.head()

ad_account_id  game_id         create_time     bid2   budget  \
0           4003  1000840 2020-01-19 16:18:31  1135.73   5000.0   
1           4003  1000840 2020-01-19 16:18:31  1135.08   5000.0   
2           4003  1000840 2020-01-19 16:24:53  1128.21   5000.0   
3           4003  1000840 2020-01-20 14:35:23  1180.24   8000.0   
4           4003  1000840 2020-01-29 18:01:59  1377.89  10000.0   

                                       schedule_time delivery_range  \
0  1111111111111111111111111111111111111111111111...          UNION   
1  1111111111111111111111111111111111111111111111...        DEFAULT   
2  1111111111111111111111111111111111111111111111...        DEFAULT   
3  1111111111111111111111111111111111111111111111...          UNION   
4  1110000000000000000011111111111111111111111111...        DEFAULT   

        flow_control_mode          smart_bid_type  adjust_cpa  cpa_bid  \
0  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.73   
1  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1135.08   
2  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1128.21   
3  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1180.24   
4  FLOW_CONTROL_MODE_FAST  SMART_BID_CONSERVATIVE         0.0  1377.89   

   hide_if_exists hide_if_converted  auto_extend_enabled       gender  \
0               0                AD                    0  GENDER_MALE   
1               0                AD                    0  GENDER_MALE   
2               0                AD                    0  GENDER_MALE   
3               0                AD                    0  GENDER_MALE   
4               0                AD                    0  GENDER_MALE   

  location_type   platform launch_price retargeting_type android_osv ios_osv  \
0       CURRENT  [ANDROID]           []             NONE        NONE    NONE   
1       CURRENT  [ANDROID]           []             NONE        NONE    NONE   
2       CURRENT  [ANDROID]           []             NONE        NONE    NONE   
3       CURRENT  [ANDROID]           []             NONE        NONE    NONE   
4       CURRENT  [ANDROID]           []             NONE        NONE    NONE   

  interest_action_mode  action_days  image_id label_ids  label  im_amount_1  \
0            UNLIMITED          NaN     19788       NaN      0          0.0   
1            UNLIMITED          NaN     19783       NaN      0          0.0   
2            UNLIMITED          NaN     19636        19      0         10.0   
3            UNLIMITED          NaN     19791       NaN      0          0.0   
4            UNLIMITED          NaN     19636        19      1         10.0   

   im_create_role_num_1  im_new_role_money_1  im_pay_role_user_num_1  \
0                   0.0                  0.0                     0.0   
1                   0.0                  0.0                     0.0   
2                  10.0                 10.0                    10.0   
3                   0.0                  0.0                     0.0   
4                  10.0                 10.0                    10.0   

   im_source_num_1  im_valid_source_num_1  im_create_role_pay_rate_1  \
0              0.0                    0.0                        NaN   
1              0.0                    0.0                        NaN   
2             10.0                    9.0                   0.029951   
3              0.0                    0.0                        NaN   
4             10.0                    9.0                   0.029951   

  im_create_role_cost_1 im_create_role_pay_cost_1  im_valid_source_rate_1  \
0                   NaN                       NaN                     NaN   
1                   NaN                       NaN                     NaN   
2                     2                         1                0.453125   
3                   NaN                       NaN                     NaN   
4                     2                         1                0.453125   

   i

In [578]:
cats_col = ['ad_account_id','game_id','schedule_time','delivery_range','flow_control_mode','smart_bid_type','hide_if_converted','gender',
           'location_type','platform','launch_price','retargeting_type','android_osv','ios_osv','interest_action_mode',
           'action_days','image_id','label_ids']
for col in cats_col:
    df[col] = df[col].astype(str)

In [579]:
test_data = df[df['create_time']>='2020-11-01']
train_data = df[df['create_time']<'2020-11-01']
# test_data = df[df['create_time']>='2020-12-01']
# train_data = df[(df['create_time']<'2020-12-01')&(df['create_time']>='2020-06-01')]
train_data.drop('create_time',axis=1,inplace=True)
test_data.drop('create_time',axis=1,inplace=True)

In [580]:
enc = ce.CatBoostEncoder(cols=cats_col).fit(train_data[cats_col],train_data['label'])
train_data[cats_col] = enc.transform(train_data[cats_col])
test_data[cats_col] = enc.transform(test_data[cats_col])

In [581]:
train_data = train_data.astype(np.float32)
test_data = test_data.astype(np.float32)
train_data.fillna(0,inplace=True)
test_data.fillna(0,inplace=True)

In [582]:
x_train = train_data.drop('label',axis=1)
y_train = train_data['label'].values
x_test = test_data.drop('label',axis=1)
y_test = test_data['label'].values

In [583]:
x_train.head()

ad_account_id  game_id         bid2   budget  schedule_time  \
0       0.262638  0.13449  1135.729980   5000.0       0.059743   
1       0.262638  0.13449  1135.079956   5000.0       0.059743   
2       0.262638  0.13449  1128.209961   5000.0       0.059743   
3       0.262638  0.13449  1180.239990   8000.0       0.059743   
4       0.262638  0.13449  1377.890015  10000.0       0.128589   

   delivery_range  flow_control_mode  smart_bid_type  adjust_cpa      cpa_bid  \
0        0.059804            0.09436        0.099066         0.0  1135.729980   
1        0.101689            0.09436        0.099066         0.0  1135.079956   
2        0.101689            0.09436        0.099066         0.0  1128.209961   
3        0.059804            0.09436        0.099066         0.0  1180.239990   
4        0.101689            0.09436        0.099066         0.0  1377.890015   

   hide_if_exists  hide_if_converted  auto_extend_enabled   gender  \
0             0.0           0.111627                  0.0  0.10057   
1             0.0           0.111627                  0.0  0.10057   
2             0.0           0.111627                  0.0  0.10057   
3             0.0           0.111627                  0.0  0.10057   
4             0.0           0.111627                  0.0  0.10057   

   location_type  platform  launch_price  retargeting_type  android_osv  \
0       0.095611  0.131022      0.117463          0.104107     0.080137   
1       0.095611  0.131022      0.117463          0.104107     0.080137   
2       0.095611  0.131022      0.117463          0.104107     0.080137   
3       0.095611  0.131022      0.117463          0.104107     0.080137   
4       0.095611  0.131022      0.117463          0.104107     0.080137   

    ios_osv  interest_action_mode  action_days  image_id  label_ids  \
0  0.104224              0.093386     0.097125  0.252528   0.122720   
1  0.104224              0.093386     0.097125  0.020221   0.122720   
2  0.104224              0.093386     0.097125  0.179254   0.103407   
3  0.104224              0.093386     0.097125  0.100100   0.122720   
4  0.104224              0.093386     0.097125  0.179254   0.103407   

   im_amount_1  im_create_role_num_1  im_new_role_money_1  \
0          0.0                   0.0                  0.0   
1          0.0                   0.0                  0.0   
2         10.0                  10.0                 10.0   
3          0.0                   0.0                  0.0   
4         10.0                  10.0                 10.0   

   im_pay_role_user_num_1  im_source_num_1  im_valid_source_num_1  \
0                     0.0              0.0                    0.0   
1                     0.0              0.0                    0.0   
2                    10.0             10.0                    9.0   
3                     0.0              0.0                    0.0   
4                    10.0             10.0                    9.0   

   im_create_role_pay_rate_1  im_create_role_cost_1  \
0                   0.000000                    0.0   
1                   0.000000                    0.0   
2                   0.029951                    2.0   
3                   0.000000                    0.0   
4                   0.029951                    2.0   

   im_create_role_pay_cost_1  im_valid_source_rate_1  im_amount_3  \
0                        0.0                0.000000          0.0   
1                        0.0                0.000000          0.0   
2                        1.0                0.453125         10.0   
3                        0.0                0.000000          0.0   
4                        1.0                0.453125         10.0   

   im_create_role_num_3  im_new_role_money_3  im_pay_role_user_num_3  \
0                   0.0                  0.0                     0.0   
1                   0.0                  0.0                     0.0   
2                  10.0                 10.0                    10.0   
3   

In [584]:
ss_columns = ['im_amount_1','im_pay_role_user_num_1','im_create_role_num_1','im_new_role_money_1','im_source_num_1','im_valid_source_num_1',
             'im_amount_3','im_pay_role_user_num_3','im_create_role_num_3','im_new_role_money_3','im_source_num_3','im_valid_source_num_3',
             'im_amount_7','im_pay_role_user_num_7','im_create_role_num_7','im_new_role_money_7','im_source_num_7','im_valid_source_num_7',
             'ad_amount_1','ad_pay_role_user_num_1','ad_create_role_num_1','ad_new_role_money_1','ad_source_num_1','ad_valid_source_num_1',
             'ad_amount_3','ad_pay_role_user_num_3','ad_create_role_num_3','ad_new_role_money_3','ad_source_num_3','ad_valid_source_num_3',
             'ad_amount_7','ad_pay_role_user_num_7','ad_create_role_num_7','ad_new_role_money_7','ad_source_num_7','ad_valid_source_num_7']

In [585]:
for col in ss_columns:
    ss = StandardScaler()
    x_train[col] = ss.fit_transform(x_train[col].values.reshape(-1,1))
    x_test[col] = ss.transform(x_test[col].values.reshape(-1,1))

In [586]:
for col in ['bid2','budget','cpa_bid']:
    ss = StandardScaler()
    x_train[col] = ss.fit_transform(x_train[col].values.reshape(-1,1))
    x_test[col] = ss.transform(x_test[col].values.reshape(-1,1))

In [587]:
x_train.head()

ad_account_id  game_id      bid2    budget  schedule_time  delivery_range  \
0       0.262638  0.13449 -1.820828 -0.059054       0.059743        0.059804   
1       0.262638  0.13449 -1.821583 -0.059054       0.059743        0.101689   
2       0.262638  0.13449 -1.829564 -0.059054       0.059743        0.101689   
3       0.262638  0.13449 -1.769123 -0.044067       0.059743        0.059804   
4       0.262638  0.13449 -1.539521 -0.034075       0.128589        0.101689   

   flow_control_mode  smart_bid_type  adjust_cpa   cpa_bid  hide_if_exists  \
0            0.09436        0.099066         0.0 -1.820828             0.0   
1            0.09436        0.099066         0.0 -1.821583             0.0   
2            0.09436        0.099066         0.0 -1.829564             0.0   
3            0.09436        0.099066         0.0 -1.769123             0.0   
4            0.09436        0.099066         0.0 -1.539521             0.0   

   hide_if_converted  auto_extend_enabled   gender  location_type  platform  \
0           0.111627                  0.0  0.10057       0.095611  0.131022   
1           0.111627                  0.0  0.10057       0.095611  0.131022   
2           0.111627                  0.0  0.10057       0.095611  0.131022   
3           0.111627                  0.0  0.10057       0.095611  0.131022   
4           0.111627                  0.0  0.10057       0.095611  0.131022   

   launch_price  retargeting_type  android_osv   ios_osv  \
0      0.117463          0.104107     0.080137  0.104224   
1      0.117463          0.104107     0.080137  0.104224   
2      0.117463          0.104107     0.080137  0.104224   
3      0.117463          0.104107     0.080137  0.104224   
4      0.117463          0.104107     0.080137  0.104224   

   interest_action_mode  action_days  image_id  label_ids  im_amount_1  \
0              0.093386     0.097125  0.252528   0.122720    -1.404390   
1              0.093386     0.097125  0.020221   0.122720    -1.404390   
2              0.093386     0.097125  0.179254   0.103407     1.804876   
3              0.093386     0.097125  0.100100   0.122720    -1.404390   
4              0.093386     0.097125  0.179254   0.103407     1.804876   

   im_create_role_num_1  im_new_role_money_1  im_pay_role_user_num_1  \
0             -1.272191            -1.081833               -1.073800   
1             -1.272191            -1.081833               -1.073800   
2              1.633456             1.890952                1.999613   
3             -1.272191            -1.081833               -1.073800   
4              1.633456             1.890952                1.999613   

   im_source_num_1  im_valid_source_num_1  im_create_role_pay_rate_1  \
0        -1.162366              -1.237989                   0.000000   
1        -1.162366              -1.237989                   0.000000   
2         1.849815               1.902499                   0.029951   
3        -1.162366              -1.237989                   0.000000   
4         1.849815               1.902499                   0.029951   

   im_create_role_cost_1  im_create_role_pay_cost_1  im_valid_source_rate_1  \
0                    0.0                        0.0                0.000000   
1                    0.0                        0.0                0.000000   
2                    2.0                        1.0                0.453125   
3                    0.0                        0.0                0.000000   
4                    2.0                        1.0                0.453125   

   im_amount_3  im_create_role_num_3  im_new_role_money_3  \
0    -1.190449             -1.230685            -1.163878   
1    -1.190449             -1.230685            -1.163878   
2     1.740042              1.803750             1.906521   
3    -1.190449             -1.230685            -1.163878   
4     1.740042              1.803750             1.906521   

   im_pay_role_user_num_3  im_source_num_3  im_valid_source_num_

In [350]:
# train_ds, val_ds = train_test_split(train_data,test_size=0.3)

In [351]:
# # 从 dataframe 导入数据 
# def df_to_dataset(df, shuffle=True, batch_size=32):
#     dfdata = df.copy()
#     if 'label' not in dfdata.columns:
#         ds = tf.data.Dataset.from_tensor_slices(dfdata.to_dict(orient = 'list'))
#     else: 
#         labels = dfdata.pop('label')
#         ds = tf.data.Dataset.from_tensor_slices((dfdata.to_dict(orient = 'list'), labels))  
#     if shuffle:
#         ds = ds.shuffle(buffer_size=len(dfdata))
#     ds = ds.batch(batch_size)
#     return ds

In [352]:
# batch_size = 50 
# train_ds = df_to_dataset(train_ds, batch_size=batch_size)
# val_ds = df_to_dataset(val_ds, shuffle=False, batch_size=batch_size)
# test_ds = df_to_dataset(test_data, shuffle=False, batch_size=batch_size)

In [550]:
x_train.shape

(21819, 2476)

In [645]:
from imblearn.over_sampling import SMOTE

In [646]:
smo = SMOTE()
x_train, y_train = smo.fit_sample(x_train, y_train)

In [674]:
x_train

ad_account_id   game_id      bid2    budget  schedule_time  \
0           0.262638  0.134490 -1.820828 -0.059054       0.059743   
1           0.262638  0.134490 -1.821583 -0.059054       0.059743   
2           0.262638  0.134490 -1.829564 -0.059054       0.059743   
3           0.262638  0.134490 -1.769123 -0.044067       0.059743   
4           0.262638  0.134490 -1.539521 -0.034075       0.128589   
...              ...       ...       ...       ...            ...   
39221       0.405055  0.134490  0.308662 -0.058115       0.135252   
39222       0.227288  0.134490 -1.203579 -0.067417       0.129375   
39223       0.030837  0.040777  1.617254 -0.034425       0.104947   
39224       0.159828  0.134490 -0.862662 -0.062049       0.117130   
39225       0.175012  0.092858 -0.157575  0.215592       0.182361   

       delivery_range  flow_control_mode  smart_bid_type  adjust_cpa  \
0            0.059804           0.094360        0.099066    0.000000   
1            0.101689           0.094360        0.099066    0.000000   
2            0.101689           0.094360        0.099066    0.000000   
3            0.059804           0.094360        0.099066    0.000000   
4            0.101689           0.094360        0.099066    0.000000   
...               ...                ...             ...         ...   
39221        0.185737           0.094360        0.105197    0.000000   
39222        0.101689           0.111651        0.099066    0.630868   
39223        0.101689           0.094360        0.099066    0.772478   
39224        0.101689           0.094360        0.105197    0.000000   
39225        0.101689           0.094360        0.105192    0.000873   

        cpa_bid  hide_if_exists  hide_if_converted  auto_extend_enabled  \
0     -1.820828             0.0           0.111627                  0.0   
1     -1.821583             0.0           0.111627                  0.0   
2     -1.829564             0.0           0.111627                  0.0   
3     -1.769123             0.0           0.111627                  0.0   
4     -1.539521             0.0           0.111627                  0.0   
...         ...             ...                ...                  ...   
39221  0.308662             0.0           0.085358                  0.0   
39222 -1.203579             0.0           0.111627                  0.0   
39223  1.617254             0.0           0.111627                  0.0   
39224 -0.862662             0.0           0.111627                  0.0   
39225 -0.157575             0.0           0.111627                  0.0   

        gender  location_type  platform  launch_price  retargeting_type  \
0      0.10057       0.095611  0.131022      0.117463          0.104107   
1      0.10057       0.095611  0.131022      0.117463          0.104107   
2      0.10057       0.095611  0.131022      0.117463          0.104107   
3      0.10057       0.095611  0.131022      0.117463          0.104107   
4      0.10057       0.095611  0.131022      0.117463          0.104107   
...        ...            ...       ...           ...               ...   
39221  0.10057       0.130107  0.131022      0.117463          0.117246   
39222  0.10057       0.117373  0.131022      0.129601          0.099519   
39223  0.10057       0.095611  0.063880      0.073709          0.094505   
39224  0.10057       0.095611  0.131022      0.097489          0.110105   
39225  0.10057       0.095611  0.063880      0.117463          0.091677   

       android_osv   ios_osv  interest_action_mode  action_days  image_id  \
0         0.080137  0.104224              0.093386     0.097125  0.252528   
1         0.080137  0.104224              0.093386     0.097125  0.020221   
2         0.080137  0.104224              0.093386     0.097125  0.179254   
3         0.080137  0.104224              0.093386     0.097125  0.100100   
4         0.080137  0.104224              0.093386     0.097125  0.179254   
...            ...       ...                   ..

In [647]:
y_train.shape

(39226,)

In [648]:
y_train.sum()

19613.0

In [649]:
tf.keras.backend.clear_session()

# 输入

# seq_input = keras.Input(shape=(seq_data.shape[1],seq_data.shape[2],), name='seq')
feature_input = tf.keras.Input(shape=(x_train.shape[1],), name='feature')

# 特征提取层
# seq_feat = layers.LSTM(128)(seq_input)
# h2 = layers.LSTM(64,return_sequences=True)(h1)
#  = layers.LSTM(32)(h1)


# feature_input = layers.Embedding(64)(feature_input)
# features = layers.concatenate([seq_feat,feature_input])

d1 = layers.BatchNormalization()(feature_input)
d1 = layers.Dropout(rate=0.4)(d1)

h1 = layers.Dense(256, activation='relu',kernel_regularizer=tf.keras.regularizers.l2(0.01))(d1)

h1 = layers.BatchNormalization()(h1)
h1 = layers.Dropout(rate=0.3)(h1)

h2 = layers.Dense(128, activation='relu')(h1)
h2 = layers.BatchNormalization()(h2)
h2 = layers.Dropout(rate=0.3)(h2)

h3 = layers.Dense(64, activation='relu')(h2)
h3 = layers.BatchNormalization()(h3)
h3 = layers.Dropout(rate=0.3)(h3)

h4 = layers.Dense(32, activation='relu')(h3)
h4 = layers.BatchNormalization()(h4)
h4 = layers.Dropout(rate=0.3)(h4)

h5 = layers.Dense(16, activation='relu')(h4)
h5 = layers.BatchNormalization()(h5)
h5 = layers.Dropout(rate=0.3)(h5)


outputs = layers.Dense(1, activation='sigmoid',name='priority')(h5)

# 构建模型
model = keras.Model(inputs=feature_input,
                    outputs=outputs)
# model.summary()                            
# 分类层
# priority_pred = layers.Dense(1, activation='sigmoid', name='priority')(features)

In [630]:
# weight_for_0 = 21819 / 19613 / 2.0
# weight_for_1 = 21819 / 2206 / 2.0
# class_weight = {0: weight_for_0, 1: weight_for_1}

In [650]:
early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_auc', 
    verbose=1,
    patience=20,
    mode='max',
    restore_best_weights=True
)

In [651]:
model.compile(optimizer='adam',
              loss='binary_crossentropy',
              metrics=['AUC'])

In [654]:
history = model.fit(x_train,y_train,
                    batch_size= 64,
                    validation_split=0.3,
                    verbose=1,
                    epochs=40,
                   callbacks=[early_stopping])

Epoch 1/40
430/430 [==============================] - 5s 13ms/step - loss: 1.6830 - auc: 0.6468 - val_loss: 1.3116 - val_auc: 0.0000e+00
Epoch 2/40
430/430 [==============================] - 4s 9ms/step - loss: 0.8249 - auc: 0.7487 - val_loss: 1.0390 - val_auc: 0.0000e+00
Epoch 3/40
430/430 [==============================] - 4s 9ms/step - loss: 0.6749 - auc: 0.7742 - val_loss: 1.0824 - val_auc: 0.0000e+00
Epoch 4/40
430/430 [==============================] - 4s 9ms/step - loss: 0.6508 - auc: 0.7843 - val_loss: 0.9932 - val_auc: 0.0000e+00
Epoch 5/40
430/430 [==============================] - 4s 9ms/step - loss: 0.6863 - auc: 0.7837 - val_loss: 1.0552 - val_auc: 0.0000e+00
Epoch 6/40
430/430 [==============================] - 4s 9ms/step - loss: 0.6377 - auc: 0.7889 - val_loss: 1.0457 - val_auc: 0.0000e+00
Epoch 7/40
430/430 [==============================] - 4s 9ms/step - loss: 0.6202 - auc: 0.7919 - val_loss: 1.0817 - val_auc: 0.0000e+00
Epoch 8/40
430/430 [===========================

In [665]:
predict_y = model.predict(x_test)

In [666]:
predict_y.max()

0.7060791

In [670]:
sum(list(map(lambda x:1 if x>=0.55 else 0,predict_y)))

438

In [613]:
y_test.sum()

723.0

In [659]:
roc_auc_score(y_test,predict_y)

0.6526849184139544

In [671]:
predict_y = list(map(lambda x:1 if x>=0.55 else 0,predict_y))

In [672]:
print(classification_report(y_test, predict_y))

              precision    recall  f1-score   support

         0.0       0.90      0.94      0.92      6020
         1.0       0.21      0.13      0.16       723

    accuracy                           0.86      6743
   macro avg       0.55      0.53      0.54      6743
weighted avg       0.83      0.86      0.84      6743

